<a href="https://colab.research.google.com/github/22Ifeoma22/22Ifeoma22/blob/main/2_Transformers.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [3]:
!pip install bertviz

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 157.6/157.6 kB 5.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.2/139.2 kB 10.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.6/12.6 MB 84.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.6/82.6 kB 6.1 MB/s eta 0:00:00


In [6]:
from  transformers import BertModel, BertTokenizer
from bertviz import head_view
import torch
import pandas as pd

In [7]:
# Let's load a vanilla Bert-base model
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained('bert-base-uncased')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

In [11]:
text = "my friend told me this class and I love it so far! she is right."

tokens = tokenizer.tokenize(text)
# Convert tokens to their corresponding numerical IDs
input_ids = tokenizer.convert_tokens_to_ids(tokens)

# Create the PyTorch tensor from the numerical IDs
inputs = torch.tensor([input_ids])  # Add an extra dimension for batch size

inputs

tensor([[2026, 2767, 2409, 2033, 2023, 2465, 1998, 1045, 2293, 2009, 2061, 2521,
          999, 2016, 2003, 2157, 1012]])

In [13]:
attention = model(inputs, output_attentions=True)[2] # Grab the attention scores from Bert

BertSdpaSelfAttention is used but `torch.nn.functional.scaled_dot_product_attention` does not support non-absolute `position_embedding_type` or `output_attentions=True` or `head_mask`. Falling back to the manual attention implementation, but specifying the manual implementation will be required from Transformers version v5.0.0 onwards. This warning can be removed using the argument `attn_implementation="eager"` when loading the model.


In [14]:
final_attention = attention[-1].mean(1)[0]

In [18]:
attention_df = pd.DataFrame(final_attention.detach()).applymap(float).round(3)
attention_df.columns = tokenizer.convert_ids_to_tokens(input_ids)
attention_df.index = tokenizer.convert_ids_to_tokens(input_ids)
attention_df # sums across rows add up to 1. sum scores columns do not

<ipython-input-18-7a5363e16693>:1: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  attention_df = pd.DataFrame(final_attention.detach()).applymap(float).round(3)


my  friend   told     me   this  class    and      i   love     it  \
my      0.519   0.016  0.003  0.001  0.005  0.006  0.007  0.004  0.002  0.001   
friend  0.122   0.138  0.035  0.013  0.023  0.023  0.029  0.015  0.016  0.020   
told    0.072   0.071  0.152  0.029  0.069  0.035  0.040  0.022  0.036  0.052   
me      0.059   0.073  0.048  0.093  0.063  0.024  0.059  0.066  0.072  0.057   
this    0.080   0.037  0.047  0.033  0.136  0.052  0.061  0.040  0.063  0.072   
class   0.117   0.036  0.027  0.015  0.086  0.156  0.044  0.023  0.043  0.063   
and     0.084   0.042  0.029  0.039  0.047  0.021  0.162  0.051  0.065  0.044   
i       0.056   0.049  0.024  0.061  0.036  0.018  0.072  0.100  0.079  0.052   
love    0.037   0.042  0.024  0.028  0.049  0.025  0.057  0.051  0.232  0.075   
it      0.037   0.039  0.021  0.031  0.072  0.054  0.061  0.044  0.074  0.211   
so      0.040   0.031  0.019  0.026  0.045  0.024  0.051  0.044  0.069  0.119   
far     0.053   0.037  0.016  0.022  0.041  0.047  0.056  0.035  0.056  0.107   
!       0.147   0.048  0.013  0.010  0.016  0.011  0.053  0.020  0.022  0.013   
she     0.097   0.121  0.024  0.009  0.016  0.021  0.022  0.017  0.015  0.017   
is      0.125   0.048  0.021  0.007  0.013  0.013  0.017  0.015  0.013  0.011   
right   0.136   0.030  0.011  0.004  0.011  0.019  0.010  0.008  0.011  0.009   
.       0.282   0.020  0.007  0.005  0.014  0.014  0.022  0.007  0.009  0.007   

           so    far      !    she     is  right      .  
my      0.001  0.003  0.052  0.051  0.051  0.041  0.237  
friend  0.007  0.019  0.086  0.202  0.090  0.070  0.092  
told    0.016  0.037  0.068  0.150  0.052  0.041  0.058  
me      0.024  0.060  0.067  0.128  0.046  0.024  0.036  
this    0.028  0.059  0.065  0.079  0.041  0.039  0.071  
class   0.017  0.049  0.060  0.084  0.041  0.045  0.095  
and     0.028  0.059  0.105  0.090  0.039  0.021  0.073  
i       0.030  0.064  0.082  0.148  0.062  0.026  0.041  
love    0.035  0.086  0.067  0.093  0.038  0.027  0.035  
it      0.065  0.118  0.045  0.060  0.018  0.018  0.032  
so      0.115  0.143  0.074  0.091  0.037  0.021  0.049  
far     0.050  0.186  0.081  0.091  0.035  0.023  0.066  
!       0.011  0.027  0.181  0.148  0.068  0.061  0.150  
she     0.010  0.020  0.082  0.239  0.122  0.097  0.073  
is      0.009  0.011  0.061  0.226  0.206  0.112  0.092  
right   0.005  0.009  0.058  0.182  0.109  0.277  0.112  
.       0.005  0.011  0.079  0.075  0.052  0.060  0.334

In [ ]:
# https://nlp.stanford.edu/pubs/clark2019what.pdf
# Layer index 2 seems to be attending to the previous token
# Layer index 6 seems to be for pronouns

In [19]:
tokens_as_list = tokenizer.convert_ids_to_tokens(inputs[0])
head_view(attention, tokens_as_list)

<IPython.core.display.Javascript object>

In [24]:
# Head 3-11 attends to previous tokens
head_view(attention, tokenizer.convert_ids_to_tokens(inputs[0]), layer=2, heads=[0])

<IPython.core.display.Javascript object>

In [28]:
# Head 8-10,relating direct object s to their verbs eg told -> me
head_view(attention, tokenizer.convert_ids_to_tokens(inputs[0]), layer=7, heads=[9])

<IPython.core.display.Javascript object>

In [32]:
# attention in the eight encoder = 10th to see directattention
eight_ten = attention[7][0][9]

In [33]:
attention_df = pd.DataFrame(eight_ten.detach()).applymap(float).round(3)
attention_df.columns = tokenizer.convert_ids_to_tokens(input_ids)
attention_df.index = tokenizer.convert_ids_to_tokens(input_ids)
attention_df

<ipython-input-33-6379c7f87a4b>:1: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  attention_df = pd.DataFrame(eight_ten.detach()).applymap(float).round(3)


my  friend   told     me   this  class    and      i   love     it  \
my      0.254   0.018  0.011  0.007  0.014  0.016  0.007  0.004  0.010  0.009   
friend  0.463   0.266  0.024  0.014  0.028  0.010  0.049  0.017  0.003  0.005   
told    0.442   0.219  0.126  0.044  0.096  0.013  0.026  0.004  0.001  0.001   
me      0.013   0.052  0.770  0.097  0.054  0.003  0.005  0.001  0.000  0.000   
this    0.003   0.027  0.644  0.147  0.151  0.012  0.008  0.001  0.002  0.000   
class   0.010   0.008  0.297  0.150  0.444  0.045  0.005  0.001  0.013  0.005   
and     0.019   0.007  0.190  0.203  0.397  0.057  0.092  0.007  0.008  0.002   
i       0.005   0.014  0.043  0.016  0.018  0.008  0.837  0.044  0.006  0.001   
love    0.011   0.003  0.015  0.002  0.005  0.004  0.700  0.189  0.057  0.006   
it      0.002   0.005  0.061  0.006  0.012  0.019  0.048  0.058  0.727  0.031   
so      0.009   0.006  0.011  0.002  0.006  0.013  0.295  0.142  0.291  0.108   
far     0.005   0.001  0.002  0.001  0.003  0.002  0.051  0.044  0.270  0.396   
!       0.052   0.006  0.004  0.002  0.003  0.011  0.122  0.053  0.046  0.105   
she     0.025   0.008  0.002  0.000  0.001  0.004  0.016  0.003  0.014  0.015   
is      0.014   0.004  0.002  0.000  0.001  0.001  0.005  0.001  0.003  0.003   
right   0.027   0.005  0.003  0.001  0.001  0.001  0.004  0.001  0.001  0.002   
.       0.014   0.001  0.003  0.001  0.003  0.003  0.000  0.000  0.000  0.001   

           so    far      !    she     is  right      .  
my      0.003  0.005  0.011  0.028  0.036  0.062  0.504  
friend  0.001  0.002  0.014  0.006  0.013  0.005  0.082  
told    0.000  0.000  0.011  0.001  0.002  0.001  0.013  
me      0.000  0.000  0.001  0.000  0.000  0.000  0.002  
this    0.000  0.000  0.001  0.000  0.001  0.001  0.003  
class   0.001  0.001  0.001  0.001  0.006  0.007  0.006  
and     0.001  0.000  0.004  0.000  0.003  0.003  0.007  
i       0.001  0.000  0.006  0.000  0.000  0.000  0.001  
love    0.001  0.001  0.003  0.000  0.000  0.000  0.001  
it      0.012  0.012  0.002  0.001  0.001  0.004  0.000  
so      0.040  0.039  0.029  0.004  0.002  0.002  0.001  
far     0.153  0.044  0.018  0.003  0.006  0.001  0.001  
!       0.132  0.096  0.276  0.040  0.017  0.014  0.022  
she     0.017  0.042  0.259  0.302  0.121  0.077  0.092  
is      0.002  0.022  0.240  0.466  0.094  0.074  0.068  
right   0.002  0.010  0.192  0.435  0.224  0.045  0.047  
.       0.000  0.001  0.012  0.084  0.107  0.327  0.444

## Introduction to Transfer Learning

NLP - A model is pretrained on an unlabeled text corpora on an unsupervised task that generally dosen't have a  "useful objective is is just meant to learn language/ context in general
- The model is then fine-tuned (updated) on a specific NLP "DOWNSTREAM"
task using a labeled dataset that is usually quite small in comparism.
- if we simply trained on the downstream smaller dataset without pretraining, we would never be able to achieve the same state of the art results
** Pretraining Bert - Corpus
- Bert book Corpus (800M words)

Replace of numpy to use the power GPU and other accelerator
- Pytorch is a python library made accessible for deep learning